In [98]:
import tensorflow as tf
import os

# set tensorflow to be less verbose
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'

print("Usandor Tensorflow version " + tf.__version__)

if tf.test.gpu_device_name():
  print('Usando GPU: {}'.format(tf.test.gpu_device_name()))
else:
  print("Usando CPU.")


Usandor Tensorflow version 2.13.1
Usando GPU: /device:GPU:0


2023-11-26 23:29:58.960750: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:995] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-11-26 23:29:58.961028: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:995] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-11-26 23:29:58.961103: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:995] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysf

In [99]:
from numpy import array, hstack
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout
import pandas as pd
from empresa4.datasets import get_dataset, nombres_datasets
from keras.callbacks import EarlyStopping
from datetime import datetime
from empresa4.core import calculate_error_2

# Data Preparation

In [100]:
# Read the data
df = get_dataset("02_productos_todos_anti_leak")
df

{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()


periodo  product_id  cust_request_qty  cust_request_tn          tn  \
0       201701       20001             479.0        937.72717   934.77222   
1       201701       20002             391.0        555.18654   550.15707   
2       201701       20003             438.0       1067.81543  1063.45835   
3       201701       20004             339.0        569.37394   555.91614   
4       201701       20005             249.0        494.60084   494.27011   
...        ...         ...               ...              ...         ...   
33691   201902       21235               0.0          0.00000     0.00000   
33692   201902       21236               0.0          0.00000     0.00000   
33693   201902       21115               0.0          0.00000     0.00000   
33694   201902       20734               0.0          0.00000     0.00000   
33695   201902       21243               0.0          0.00000     0.00000   

      product_category         cat2  sku_size  plan_precios_cuidados  
0                   HC  ROPA LAVADO    3000.0                      0  
1                   HC  ROPA LAVADO    3000.0                      0  
2                FOODS     ADEREZOS     475.0                      0  
3                FOODS     ADEREZOS     240.0                      0  
4                FOODS     ADEREZOS     120.0                      0  
...                ...          ...       ...                    ...  
33691               PC        PIEL1     200.0                      0  
33692               PC        PIEL1     400.0                      0  
33693               PC         DEOS      89.0                      0  
33694               PC      CABELLO     400.0                      0  
33695               PC         DEOS      70.0                      0  

[33696 rows x 9 columns]

In [101]:
cluster_df = pd.read_csv("product_ids_clusters.csv")
cluster_df

{'axis': -1, 'kind': None, 'order': None}
()


product_id  201701_norm  201702_norm  201703_norm  201704_norm  \
0          20001     0.091342     0.347663     0.567846     0.466153   
1          20002     0.035110     0.286313     0.472443     0.295634   
2          20003     0.375239     0.383889     0.468175     0.268330   
3          20004     0.164645     0.400644     0.386223     0.403683   
4          20005     0.179476     0.441811     0.451804     0.530902   
...          ...          ...          ...          ...          ...   
1291       21295     1.000000     0.000000     0.000000     0.000000   
1292       21296     0.000000     0.000000     0.000000     0.000000   
1293       21297     1.000000     0.000000     0.000000     0.000000   
1294       21298     0.000000     0.000000     0.000000     0.000000   
1295       21299     0.000000     0.000000     0.000000     0.000000   

      201705_norm  201706_norm  201707_norm  201708_norm  201709_norm  ...  \
0        0.654484     0.662267     0.449035     0.552176     0.573766  ...   
1        0.477368     0.547960     0.478475     0.350738     0.602969  ...   
2        0.316705     0.379824     0.400778     0.441167     0.748375  ...   
3        0.428377     0.465553     0.449286     0.822024     0.993244  ...   
4        0.413083     0.423504     0.501455     0.855840     1.000000  ...   
...           ...          ...          ...          ...          ...  ...   
1291     0.000000     0.000000     0.000000     0.000000     0.000000  ...   
1292     0.000000     0.000000     0.000000     1.000000     0.000000  ...   
1293     0.000000     0.000000     0.000000     0.000000     0.000000  ...   
1294     0.000000     0.000000     0.000000     1.000000     0.000000  ...   
1295     0.000000     0.000000     0.000000     1.000000     0.000000  ...   

      201806_norm  201807_norm  201808_norm  201809_norm  201810_norm  \
0        0.501371     0.640632     0.784656     0.626804     1.000000   
1        0.585130     0.553193     0.657610     0.540080     0.780210   
2        0.337259     0.334958     0.488019     0.465740     0.670507   
3        0.353047     0.515169     0.738344     0.748157     0.638388   
4        0.438761     0.402467     0.701053     0.610395     0.716162   
...           ...          ...          ...          ...          ...   
1291     0.000000     0.000000     0.000000     0.000000     0.000000   
1292     0.000000     0.000000     0.000000     0.000000     0.000000   
1293     0.000000     0.000000     0.000000     0.000000     0.000000   
1294     0.000000     0.000000     0.000000     0.000000     0.000000   
1295     0.000000     0.000000     0.000000     0.000000     0.000000   

      201811_norm  201812_norm  201901_norm  201902_norm  cluster  
0        0.789908     0.647724     0.555827     0.548559        0  
1        1.000000     0.571334     0.716985     0.590329        0  
2        0.616162     0.392968     0.492512     0.387094        0  
3        0.632612     0.461655     0.403118     0.348204        0  
4        0.375956     0.298511     0.291258     0.328378        0  
...           ...          ...          ...          ...      ...  
1291     0.000000     0.000000     0.000000     0.000000        3  
1292     0.000000     0.000000     0.000000     0.000000        1  
1293     0.000000     0.000000     0.000000     0.000000        3  
1294     0.000000     0.000000     0.000000     0.000000        1  
1295     0.000000     0.000000     0.000000     0.000000        1  

[1296 rows x 28 columns]

In [102]:
# add column cluster from cluster_df to df
df = df.merge(cluster_df[["product_id", "cluster"]], on='product_id', how='left')
df["cluster"].isna().sum()

0

In [103]:
equiv = {
    201701: 201703,
    201702: 201704,
    201703: 201705,
    201704: 201706,
    201705: 201707,
    201706: 201708,
    201707: 201709,
    201708: 201710,
    201709: 201711,
    201710: 201712,
    201711: 201801,
    201712: 201802,
    201801: 201803,
    201802: 201804,
    201803: 201805,
    201804: 201806,
    201805: 201807,
    201806: 201808,
    201807: 201809,
    201808: 201810,
    201809: 201811,
    201810: 201812,
    201811: 201901,
    201812: 201902,
    201901: 201903,
    201902: 201904,
    201903: 201905,
    201904: 201906,
    201905: 201907,
    201906: 201908,
    201907: 201909,
    201908: 201910,
    201909: 201911,
    201910: 201912,
    201911: 202001,
    201912: 202002,
    202001: 202003,
    202002: 202004,
}
target_df = get_dataset("02_productos_todos")


# Filter data up to 201902
def lag_target_class(row):
    # from the column "periodo" and "product_id" of this row, get the equivalen periodo in equiv and get the tn column from "target" df for this product_id and the equiv periodo
    product_id = row["product_id"]
    periodo = row["periodo"]
    periodo_equiv = equiv.get(periodo)
    if periodo_equiv is None:
        return None
    value = target_df[(target_df["product_id"] == product_id) & (target_df["periodo"] == periodo_equiv)]["tn"].values[0]
    return value

{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()


In [104]:
df["target"] = df.apply(lag_target_class, axis=1)
df

periodo  product_id  cust_request_qty  cust_request_tn          tn  \
0       201701       20001             479.0        937.72717   934.77222   
1       201701       20002             391.0        555.18654   550.15707   
2       201701       20003             438.0       1067.81543  1063.45835   
3       201701       20004             339.0        569.37394   555.91614   
4       201701       20005             249.0        494.60084   494.27011   
...        ...         ...               ...              ...         ...   
33691   201902       21235               0.0          0.00000     0.00000   
33692   201902       21236               0.0          0.00000     0.00000   
33693   201902       21115               0.0          0.00000     0.00000   
33694   201902       20734               0.0          0.00000     0.00000   
33695   201902       21243               0.0          0.00000     0.00000   

      product_category         cat2  sku_size  plan_precios_cuidados  cluster  \
0                   HC  ROPA LAVADO    3000.0                      0        0   
1                   HC  ROPA LAVADO    3000.0                      0        0   
2                FOODS     ADEREZOS     475.0                      0        0   
3                FOODS     ADEREZOS     240.0                      0        0   
4                FOODS     ADEREZOS     120.0                      0        0   
...                ...          ...       ...                    ...      ...   
33691               PC        PIEL1     200.0                      0        1   
33692               PC        PIEL1     400.0                      0        1   
33693               PC         DEOS      89.0                      0        1   
33694               PC      CABELLO     400.0                      0        1   
33695               PC         DEOS      70.0                      0        1   

           target  
0      1303.35771  
1       834.73521  
2       917.16548  
3       489.91328  
4       563.89955  
...           ...  
33691     0.00000  
33692     0.00000  
33693     0.00000  
33694     0.00000  
33695     0.00000  

[33696 rows x 11 columns]

In [105]:
# Sort by `periodo` just to be sure
product_data = df.sort_values(["product_id", "periodo"])

In [106]:
# Using scikit-learn, ONE HOT ENCODE the categorical variables: product_category
product_data = pd.get_dummies(product_data, columns=["product_category", "cat2"])

# sort columns so that 'lag_tn' is the last column in the dataframe
product_data = product_data[[col for col in product_data.columns if col != 'target'] + ['target']]

{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()


In [107]:
columns = product_data.columns
product_category_columns = [col for col in columns if col.startswith("product_category")]

# convert boolean columns to int
product_data = product_data.astype({col: 'int32' for col in product_category_columns})

In [108]:
# convert bool columns to int
cat2_columns = [col for col in columns if col.startswith("cat2")]

product_data = product_data.astype({col: 'int32' for col in cat2_columns})
product_data.dtypes.sort_values()

{}
()


cat2_CABELLO                  int32
cat2_OTROS                    int32
cat2_HOGAR                    int32
cat2_DEOS                     int32
cat2_DENTAL                   int32
cat2_unknown                  int32
cat2_ADEREZOS                 int32
product_category_unknown      int32
product_category_REF          int32
cat2_PIEL1                    int32
product_category_PC           int32
product_category_FOODS        int32
cat2_PROFESIONAL              int32
cat2_ROPA ACONDICIONADOR      int32
cat2_ROPA LAVADO              int32
cat2_ROPA MANCHAS             int32
cat2_SOPAS Y CALDOS           int32
cat2_TE                       int32
cat2_VAJILLA                  int32
product_category_HC           int32
cat2_PIEL2                    int32
periodo                       int64
plan_precios_cuidados         int64
product_id                    int64
cluster                       int64
sku_size                    float64
tn                          float64
cust_request_tn             

In [109]:
product_data.isna().sum()

periodo                     0
product_id                  0
cust_request_qty            0
cust_request_tn             0
tn                          0
sku_size                    0
plan_precios_cuidados       0
cluster                     0
product_category_FOODS      0
product_category_HC         0
product_category_PC         0
product_category_REF        0
product_category_unknown    0
cat2_ADEREZOS               0
cat2_CABELLO                0
cat2_DENTAL                 0
cat2_DEOS                   0
cat2_HOGAR                  0
cat2_OTROS                  0
cat2_PIEL1                  0
cat2_PIEL2                  0
cat2_PROFESIONAL            0
cat2_ROPA ACONDICIONADOR    0
cat2_ROPA LAVADO            0
cat2_ROPA MANCHAS           0
cat2_SOPAS Y CALDOS         0
cat2_TE                     0
cat2_VAJILLA                0
cat2_unknown                0
target                      0
dtype: int64

In [110]:
product_data.columns

Index(['periodo', 'product_id', 'cust_request_qty', 'cust_request_tn', 'tn',
       'sku_size', 'plan_precios_cuidados', 'cluster',
       'product_category_FOODS', 'product_category_HC', 'product_category_PC',
       'product_category_REF', 'product_category_unknown', 'cat2_ADEREZOS',
       'cat2_CABELLO', 'cat2_DENTAL', 'cat2_DEOS', 'cat2_HOGAR', 'cat2_OTROS',
       'cat2_PIEL1', 'cat2_PIEL2', 'cat2_PROFESIONAL',
       'cat2_ROPA ACONDICIONADOR', 'cat2_ROPA LAVADO', 'cat2_ROPA MANCHAS',
       'cat2_SOPAS Y CALDOS', 'cat2_TE', 'cat2_VAJILLA', 'cat2_unknown',
       'target'],
      dtype='object')

In [111]:
product_data["periodo"].value_counts()

{}
()


periodo
201701    1296
201702    1296
201901    1296
201812    1296
201811    1296
201810    1296
201809    1296
201808    1296
201807    1296
201806    1296
201805    1296
201804    1296
201803    1296
201802    1296
201801    1296
201712    1296
201711    1296
201710    1296
201709    1296
201708    1296
201707    1296
201706    1296
201705    1296
201704    1296
201703    1296
201902    1296
Name: count, dtype: int64

# Train Test Validation Split

In [112]:
train_df = product_data[product_data["periodo"] <= 201811].copy()
validation_df = product_data[product_data["periodo"] <= 201812].copy()
test_df = product_data[product_data["periodo"] <= 201902].copy()

{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()


In [113]:
train_df.shape, validation_df.shape, test_df.shape

((29808, 30), (31104, 30), (33696, 30))

In [114]:
# standarize the data
from sklearn.preprocessing import StandardScaler

scaler_train = StandardScaler()
scaler_validation = StandardScaler()
scaler_test_product_id = StandardScaler()
scaler_test_target = StandardScaler()
scaler_test_rest = StandardScaler()

train_df[train_df.columns] = scaler_train.fit_transform(train_df[train_df.columns])
validation_df[validation_df.columns] = scaler_validation.fit_transform(validation_df[validation_df.columns])

rest = [col for col in test_df.columns if col not in ["product_id", "target"]]

test_df[rest] = scaler_test_rest.fit_transform(test_df[rest])
test_df["target"] = scaler_test_target.fit_transform(test_df[["target"]])
test_df["product_id"] = scaler_test_product_id.fit_transform(test_df[["product_id"]])

# Iterations Functions

In [115]:
from numpy import array

def split_sequences_by_product(sequences, n_steps_in, n_steps_out, product_id_idx):
    X, y = list(), list()
    unique_products = set(sequences[:, product_id_idx])
    
    for product in unique_products:
        # Filter the sequences for the current product
        product_sequences = sequences[sequences[:, product_id_idx] == product]

        # Apply the existing split_sequences logic to this filtered dataset
        for i in range(len(product_sequences)):
            # find the end of this pattern
            end_ix = i + n_steps_in
            out_end_ix = end_ix + n_steps_out
            # check if we are beyond the dataset
            if out_end_ix > len(product_sequences):
                break
            # gather input and output parts of the pattern
            # We exclude the product_id column from the inputs
            seq_x, seq_y = product_sequences[i:end_ix, :product_id_idx] + product_sequences[i:end_ix, product_id_idx+1:], product_sequences[end_ix-1:out_end_ix-1, -1]
            X.append(seq_x)
            y.append(seq_y)
    
    return array(X), array(y)

In [116]:
def get_n_neurons(n_layer, n_neurons, embudo_1, embudo_2, embudo_3):
    if n_layer == 1:
        return n_neurons
    elif n_layer == 2:
        return int(n_neurons // embudo_1)
    elif n_layer == 3:
        return int(n_neurons // embudo_2)
    elif n_layer == 4:
        return int(n_neurons // embudo_3)
    else:
        return int(n_neurons // embudo_3)

def train_model(n_layers, n_neurons, dropout_threshold, embudo_1, embudo_2, embudo_3, X_train, y_train, X_validate, y_validate):
    print(f"Training model with {n_layers} layers, {n_neurons} neurons, {embudo_1} embudo_1, {embudo_2} embudo_2, and {embudo_3} embudo_3.")

    # Number of features (excluding the target variable)
    n_features = X_train.shape[2]
    n_steps = X_train.shape[1]
    print(f"Número de features: {n_features}")

    # Define the LSTM model structure based on the number of layers
    model = Sequential()
    for i in range(n_layers):
        if i == n_layers - 1: # Last layer
            model.add(LSTM(n_neurons, activation="relu", input_shape=(n_steps, n_features)))
        else: # Intermediate layers
            final_n_neurons = get_n_neurons(i, n_neurons, embudo_1, embudo_2, embudo_3)
            model.add(LSTM(final_n_neurons, activation="relu", return_sequences=True, input_shape=(n_steps, n_features)))
            model.add(Dropout(dropout_threshold))
    
    model.add(Dense(1))
    model.compile(optimizer="adam", loss="mse")

    # Define EarlyStopping callback
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)

    # Fit the model
    model.fit(X_train, y_train, epochs=200, validation_data=(X_validate, y_validate), callbacks=[early_stopping], verbose=0)
    return model

In [117]:
def make_predictions(model, X_test, n_steps_in):
    rows = []
    # for each product_id, generate a prediction for 201904
    for i, product in enumerate(X_test["product_id"].unique()):

        this_X_test = X_test[X_test["product_id"] == product].copy()
        this_X_test, _ = split_sequences_by_product(this_X_test.values, n_steps_in, 1, 1)

        # get the last sequence from this_X_test but reshape it so that it has 1 sample, n_steps_in timesteps, and n_features features
        this_X_test = this_X_test[-1].reshape(1, n_steps_in, this_X_test.shape[2])


        # Make prediction
        yhat = model.predict(this_X_test, verbose=0)
        if yhat[0][0] < 1:
            yhat[0][0] = 0

        # Append to final output DataFrame
        rows.append(
            {
                "product_id": product,
                "target": yhat[0][0],
            }
        )
        
    final_output = pd.DataFrame(
        rows,
        columns=["product_id", "target"],
    )
    final_output = final_output.sort_values("product_id", ascending=True)
    timestamp = datetime.now().timestamp()
    final_output.to_csv(f"./output/output_lstm9_BO_{timestamp}.csv", index=False)
    return final_output

In [118]:
def calculate_score(predictions):
    # revert the standarization for the output
    predictions["target"] = scaler_test_target.inverse_transform(predictions[["target"]])
    predictions["product_id"] = scaler_test_product_id.inverse_transform(predictions[["product_id"]])
    
    predictions["product_id"] = predictions["product_id"].astype(int)
    predictions.rename(columns={"target": "prediction"}, inplace=True)
    
    return calculate_error_2(predictions, 201904)


# Bayesian Optimization

In [119]:
import pandas as pd
import optuna

In [120]:
def objective(trial):
    # Define the search space using Optuna
    n_layers = trial.suggest_int('n_layers', 1, 4)
    n_neurons = trial.suggest_int('n_neurons', 20, 500)
    n_steps_in = trial.suggest_int('n_steps_in', 2, 20)
    embudo_1 = trial.suggest_float('embudo_1', 0.9, 1.5)
    embudo_2 = trial.suggest_float('embudo_2', 0.8, 2.5)
    embudo_3 = trial.suggest_float('embudo_3', 0.7, 3.5)
    dropout_threshold = trial.suggest_float('dropout_threshold', 0.1, 0.66)

    # Your existing logic to train and evaluate the model
    X_train, y_train = split_sequences_by_product(train_df.values, n_steps_in, 1, 1)
    X_validate, y_validate = split_sequences_by_product(validation_df.values, n_steps_in, 1, 1)
    # X_test, _ = split_sequences_by_product(test_df.values, n_steps_in, 1, 1)

    model = train_model(n_layers, n_neurons, dropout_threshold, embudo_1, embudo_2, embudo_3, X_train, y_train, X_validate, y_validate)
    predictions = make_predictions(model, test_df, n_steps_in)
    score = calculate_score(predictions)

    # Save the results
    result = {
        "n_layers": n_layers,
        "n_neurons": n_neurons,
        "n_steps_in": n_steps_in,
        "embudo_1": embudo_1,
        "embudo_2": embudo_2,
        "embudo_3": embudo_3,
        "dropout_threshold": dropout_threshold,
        "score": score
    }
    g_s_df = pd.DataFrame([result])
    g_s_df.to_csv(f"./output/lstm_9_optuna_{n_layers}_{n_neurons}_{dropout_threshold}_{score}.csv", mode='a', index=False)
    print("Result: ", result)
    return score

In [121]:
# Create a study object and specify the optimization direction
study = optuna.create_study(direction='minimize', study_name="lstm_9_BO")

# Perform optimization
study.optimize(objective, n_trials=50)

# Extract the best trial
best_trial = study.best_trial

print('Best trial:')
for key, value in best_trial.params.items():
    print(f"{key}: {value}")

[I 2023-11-26 23:30:05,504] A new study created in memory with name: lstm_9_BO


{'out': None}
(1, 4)
{'out': None}
(20, 500)
{'out': None}
(2, 20)
Training model with 1 layers, 338 neurons, 1.1699430387001644 embudo_1, 2.3227529220570853 embudo_2, and 3.13546199778468 embudo_3.
Número de features: 28


{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -

[I 2023-11-26 23:32:34,537] Trial 0 finished with value: 1.0738913640383425 and parameters: {'n_layers': 1, 'n_neurons': 338, 'n_steps_in': 8, 'embudo_1': 1.1699430387001644, 'embudo_2': 2.3227529220570853, 'embudo_3': 3.13546199778468, 'dropout_threshold': 0.4894844851383632}. Best is trial 0 with value: 1.0738913640383425.


{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
Result:  {'n_layers': 1, 'n_neurons': 338, 'n_steps_in': 8, 'embudo_1': 1.1699430387001644, 'embudo_2': 2.3227529220570853, 'embudo_3': 3.13546199778468, 'dropout_threshold': 0.4894844851383632, 'score': 1.0738913640383425}
{'out': None}
(1, 4)
{'out': None}
(20, 500)
{'out': None}
(2, 20)
Training model with 3 layers, 465 neurons, 1.2610031838598612 embudo_1, 1.5488324578418484 embudo_2, and 1.362905415741249 embudo_3.
Número de features: 28
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axi

...

{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
Result:  {'n_layers': 3, 'n_neurons': 297, 'n_steps_in': 4, 'embudo_1': 1.1429150443405978, 'embudo_2': 1.4890243257437397, 'embudo_3': 1.2999799409856552, 'dropout_threshold': 0.5409071195415692, 'score': 1.1387861649665698}
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'out': None}
(0.5714285714285714, 4.0)
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'out': None}
(0.08888888888888889, 4.0)
{'decimals': 0, 'out': None}
()
{'out': None}
(1, 4)
{'decimals': 0, 'out': None}
()
{'out': None}
(

[I 2023-11-27 01:59:33,585] Trial 48 finished with value: 1.1825978911506168 and parameters: {'n_layers': 4, 'n_neurons': 499, 'n_steps_in': 7, 'embudo_1': 1.0715645805276621, 'embudo_2': 1.8609078935550276, 'embudo_3': 0.9120622657694025, 'dropout_threshold': 0.5731350565743832}. Best is trial 39 with value: 1.0541424916772666.


{}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
Result:  {'n_layers': 4, 'n_neurons': 499, 'n_steps_in': 7, 'embudo_1': 1.0715645805276621, 'embudo_2': 1.8609078935550276, 'embudo_3': 0.9120622657694025, 'dropout_threshold': 0.5731350565743832, 'score': 1.1825978911506168}
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'out': None}
(0.5714285714285714, 4.0)
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'out': None}
(0.08695652173913043, 4.0)
{'decimals': 0, 'out': None}
()
{'out': None}
(1, 4)
{'decimals': 0, 'out': None}
()
{'out': None}
(1, 4)
{'axis': None, 'out': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'out': None}
(68.71428571428571, 481.0)
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1,

[I 2023-11-27 02:02:18,236] Trial 49 finished with value: 1.2416231858825257 and parameters: {'n_layers': 3, 'n_neurons': 354, 'n_steps_in': 15, 'embudo_1': 1.1179943204008997, 'embudo_2': 1.7570360870789394, 'embudo_3': 1.126992017575641, 'dropout_threshold': 0.6219342867602082}. Best is trial 39 with value: 1.0541424916772666.


{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': -1, 'kind': None, 'order': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
{'axis': None, 'dtype': None, 'out': None}
()
Result:  {'n_layers': 3, 'n_neurons': 354, 'n_steps_in': 15, 'embudo_1': 1.1179943204008997, 'embudo_2': 1.7570360870789394, 'embudo_3': 1.126992017575641, 'dropout_threshold': 0.6219342867602082, 'score': 1.2416231858825257}
Best trial:
n_layers: 3
n_neurons: 287
n_steps_in: 2
embudo_1: 1.1080750394892227
embudo_2: 1.8625519622799758
embudo_3: 1.062200745375922
dropout_threshold: 0.5585096867594589


In [122]:
# import pandas as pd

# predictions = pd.read_csv("./output/output_lstm9_BO_1700947337.071307.csv")
# predictions["target"] = scaler_test_target.inverse_transform(predictions[["target"]])
# predictions["product_id"] = scaler_test_product_id.inverse_transform(predictions[["product_id"]])
    
# predictions["product_id"] = predictions["product_id"].astype(int)

# predictions.rename(columns={"target": "prediction"}, inplace=True)
# # convert numbers under 27 in column "prediction" to 0
# predictions.loc[predictions["prediction"] < 27, "prediction"] = 0

# predictions


In [123]:
calculate_error_2(predictions, 201904)

NameError: name 'predictions' is not defined